### モデルの形式 (.ckpt/.safetensors) を相互変換するスクリプトです
#### SD2.x系付属の.yamlも併せて変換します
#### オプションでfp16として保存できます

最初に以下のコードを実行

In [ ]:
!pip install torch safetensors
!pip install pytorch-lightning
!pip install wget

Google Drive上のファイルを読み書きしたい場合は、以下のコードを実行

In [ ]:
from google.colab import drive
drive.mount("/content/drive")

<details><summary><font size="-0">変換したモデルをHugging Faceに投稿したい場合は、以下のコードを実行</font></summary>

1. [このページ](https://huggingface.co./settings/tokens)にアクセスしてNew tokenからName=適当, Role=writeでAccess Tokenを取得

2. 取得したTokenをコピー & 実行後に出現する以下の欄に貼り付け & Login
</details>

In [ ]:
!pip install huggingface_hub
from huggingface_hub import login
login()

以下のリンク等を任意のものに差し替えてから、以下のコードを上から順番に両方とも実行

In [ ]:
#@title <font size="-0">モデルをダウンロード</font>
#@markdown {Google Drive上のモデル名 or モデルのダウンロードリンク} をカンマ区切りで任意個指定
#@markdown - Drive上のモデル名の場合...My Driveに対する相対パスで指定
#@markdown - ダウンロードリンクの場合...Hugging Face等のダウンロードリンクを右クリック & リンクのアドレスをコピー & 下のリンクの代わりに貼り付け
import shutil
import urllib.parse
import urllib.request
import wget
import os

models = "Specify_the_model_in_this_way_if_the_model_is_on_My_Drive.safetensors, https://huggingface.co./hakurei/waifu-diffusion-v1-4/resolve/main/wd-1-4-anime_e1.ckpt, https://huggingface.co./hakurei/waifu-diffusion-v1-4/resolve/main/wd-1-4-anime_e1.yaml" #@param {type:"string"}
models = [m.strip() for m in models.split(",")]
for model in models:
  if 0 < len(urllib.parse.urlparse(model).scheme): # if model is url
    wget.download(model)
  elif model.endswith((".ckpt", ".safetensors", ".yaml", ".pt")):
    shutil.copy("/content/drive/MyDrive/" + model, "/content/" + os.path.basename(model)) # get the model from mydrive
  else:
    print(f"\"{model}\"はURLではなく、正しい形式のファイルでもありません")

In [ ]:
#@title <font size="-0">モデルを変換</font>
#@markdown 変換するモデルをカンマ区切りで任意個指定<br>
#@markdown 何も入力されていない場合は、読み込まれている全てのモデルが変換される
import os
import glob
import torch
import safetensors.torch
from functools import partial

from sys import modules
if "huggingface_hub" in modules:
  from huggingface_hub import HfApi, Repository

models = "wd-1-4-anime_e1.ckpt, wd-1-4-anime_e1.yaml" #@param {type:"string"}
pruning = True #@param {type:"boolean"}
as_fp16 = True #@param {type:"boolean"}
clip_fix = "fix err key" #@param ["off", "fix err key", "del err key"]
uninvited_key = "cond_stage_model.transformer.text_model.embeddings.position_ids"
save_type = ".safetensors" #@param [".safetensors", ".ckpt"]
merge_vae = "" #@param ["", "vae-ft-mse-840000-ema-pruned.ckpt", "kl-f8-anime.ckpt", "kl-f8-anime2.ckpt", "Anything-V3.0.vae.pt"] {allow-input: true}
save_directly_to_Google_Drive = False #@param {type:"boolean"}
#@markdown 変換したモデルをHugging Faceに投稿する場合は「yourname/yourrepo」の形式で投稿先リポジトリを指定<br>
#@markdown 投稿しない場合は何も入力しない<br>
# 5GB以上のファイルを投稿する場合は、投稿先リポジトリを丸ごとダウンロードする工程が挟まるので、時間がかかる場合があります
repo_id = "" #@param {type:"string"}

vae_preset = {
    "vae-ft-mse-840000-ema-pruned.ckpt": "https://huggingface.co./stabilityai/sd-vae-ft-mse-original/resolve/main/vae-ft-mse-840000-ema-pruned.ckpt",
    "kl-f8-anime.ckpt": "https://huggingface.co./hakurei/waifu-diffusion-v1-4/resolve/main/vae/kl-f8-anime.ckpt",
    "kl-f8-anime2.ckpt": "https://huggingface.co./hakurei/waifu-diffusion-v1-4/resolve/main/vae/kl-f8-anime2.ckpt",
    "Anything-V3.0.vae.pt": "https://huggingface.co./Linaqruf/anything-v3.0/resolve/main/Anything-V3.0.vae.pt"}
if (merge_vae in vae_preset) & (not os.path.exists(merge_vae)):
  wget.download(vae_preset[merge_vae])

def upload_to_hugging_face(file_name):
  api = HfApi()
  api.upload_file(path_or_fileobj=file_name,
    path_in_repo=file_name,
    repo_id=repo_id,
  )

def convert_yaml(file_name):
  with open(file_name) as f:
    yaml = f.read()
  if save_directly_to_Google_Drive:
    os.chdir("/content/drive/MyDrive")
  is_safe = save_type == ".safetensors"
  yaml = yaml.replace(f"use_checkpoint: {is_safe}", f"use_checkpoint: {not is_safe}")
  if as_fp16:
    yaml = yaml.replace("use_fp16: False", "use_fp16: True")
    file_name = os.path.splitext(file_name)[0] + "-fp16.yaml"
  with open(file_name, mode="w") as f:
    f.write(yaml)
  if repo_id != "":
    upload_to_hugging_face(file_name)
  os.chdir("/content")

#use `str.removeprefix(p)` in python 3.9+
def remove_prefix(input_string, prefix):
  if prefix and input_string.startswith(prefix):
    return input_string[len(prefix):]
  return input_string

if models == "":
  models = [os.path.basename(m) for m in glob.glob(r"/content/*.ckpt") + glob.glob(r"/content/*.safetensors") + glob.glob(r"/content/*.yaml")]
else:
  models = [m.strip() for m in models.split(",")]

for model in models:
  model_name, model_ext = os.path.splitext(model)
  if model_ext == ".yaml":
    convert_yaml(model)
  elif (model_ext != ".safetensors") & (model_ext != ".ckpt"):
    print("対応形式は.ckpt及び.safetensors並びに.yamlのみです\n" + f"\"{model}\"は対応形式ではありません")
  else:
    load_model = lambda filename: partial(safetensors.torch.load_file, device="cpu")(filename) if os.path.splitext(filename)[1] == ".safetensors" else partial(torch.load, map_location=torch.device("cpu"))(filename)
    save_model = safetensors.torch.save_file if save_type == ".safetensors" else torch.save
    # convert model
    with torch.no_grad():
      weights = load_model(model)
      if "state_dict" in weights:
        weights = weights["state_dict"]
      if pruning:
        model_name += "-pruned"
        for key in list(weights.keys()):
          if key.startswith("model_ema."):
            del weights[key]
      if as_fp16:
        model_name += "-fp16"
        for key in weights.keys():
          weights[key] = weights[key].half()
      if uninvited_key in weights:
        if clip_fix == "del err key":
          del weights[uninvited_key]
        if clip_fix == "fix err key":
          weights[uninvited_key] = torch.tensor([list(range(77))],dtype=torch.int64)
      if merge_vae != "":
        vae_weights = load_model(merge_vae)
        if "state_dict" in vae_weights:
          vae_weights = vae_weights["state_dict"]
        for key in weights.keys():
          if key.startswith("first_stage_model."):
            weights[key] = vae_weights[remove_prefix(key, "first_stage_model.")]
        del vae_weights
      if save_directly_to_Google_Drive:
        os.chdir("/content/drive/MyDrive")
      save_model(weights, saved_model := model_name + save_type)
      if repo_id != "":
        if os.path.getsize(saved_model) >= 5*1000*1000*1000:
          with Repository(os.path.basename(repo_id), clone_from=repo_id, skip_lfs_files=True, token=True).commit(commit_message=f"Upload {saved_model} with huggingface_hub", blocking=False):
            save_model(weights, saved_model)
        else:
          upload_to_hugging_face(saved_model)
      os.chdir("/content")
      del weights

!reset

SD2.x系モデル等を変換する場合は、付属の設定ファイル (モデルと同名の.yamlファイル) も同時にダウンロード/変換しましょう

指定方法はモデルと同じです

メモリ不足でクラッシュする場合は、より小さいモデルを利用するか、有料のハイメモリランタイムを使用すること

標準では10GBまでのモデルを変換できます

Hugging Faceに5GB以上のファイルを投稿する場合はメモリ消費量が約2倍になります

[モデルのリンク集](https://huggingface.co./models?other=stable-diffusion)等から好きなモデルを選ぼう